## Complétion de matrices symétriques semi-définie positive


Soient $A\in \mathcal{S}_n(\mathbb{R})$ semi-définie positive. On suppose ne connaitre qu'un certain nombre d'entrées de cette matrice : $\forall (i,j)\in\Omega, \quad A_{i,j} $ est connu.

On cherche à trouver les données manquantes (complétion de matrice). On modélise ce problème par 

$$\hspace{5cm} (\mathcal{E})\quad \mbox{ Trouver }\Delta \in \mathcal{S}_n^+(\mathbb{R}) \mbox{ t.q. } \forall (i,j)\in\Omega, \quad \Delta_{i,j}=A_{i,j}.$$

On cherche ainsi  $$\Delta \in \mathcal{C}=\mathcal{C}_1\bigcap\mathcal{C}_2,$$ avec $$\mathcal{C}_1=\mathcal{S}_n^+(\mathbb{R}), \quad \mathcal{C}_2=\left\{\Delta \in \mathcal{M}_n(\mathbb{R}) \mbox{ t.q. } \forall (i,j)\in\Omega,  \Delta_{i,j}=A_{i,j}\right\}.$$ 

**Question 1 :** Justifier que ces deux parties sont convexes, fermées et non vides.


On définit pour cela le problème d'optimisation suivant : 
$$\hspace{5cm} (\mathcal{P})\quad \min_{\Delta \in \mathcal{M}_n(\mathbb{R})} f(\Delta)=\max(d(\Delta,\mathcal{C}_1),d(\Delta,\mathcal{C}_2))$$

avec $d(\Delta,\mathcal{C}_i)$ la distance de $\Delta$ à $\mathcal{C}_i$.

**Question 2 :** On choisit de munir $\mathcal{M}_n(\mathbb{R})$ du produit scalaire $<X,Y>=tr(XY^T)$. On a alors $d(\Delta,\mathcal{C}_i)=\Vert \Delta - \Pi_{\mathcal{C}_i}(\Delta)\Vert_F$, avec $\Vert \Vert_F$ la norme de Frobenius, et $\Pi_{\mathcal{C}_i}(\Delta)$ le projeté de $\Delta$ sur $\mathcal{C}_i$. Donner l'expression analytique des $\Pi_{\mathcal{C}_i}(\Delta)$.

**Question 3 :** Proposer un sous-gradient de $f$ en $\Delta$.

**Qestion 4 :** Résoudre le problème $ (\mathcal{E})$ par l'algorithme du sous-gradient.


In [21]:
## Import de packages
using Plots, Random, LinearAlgebra

In [93]:
n = 100
nd = 50

#Construction de la matrice A
tmp = randn(n, 2 * n)
F = qr(tmp)
P = F.Q[1:n, 1:n]
d = abs.(10 * randn(n,))
A = P * Diagonal(d) * P'

#Indice des entrées connues
Oi = randperm(n)[1:min(nd, n)]
Ω = zip(Oi, Oi)

println(Oi)


[66, 6, 94, 56, 59, 73, 38, 63, 34, 5, 2, 84, 25, 35, 52, 80, 58, 92, 91, 16, 42, 86, 81, 24, 72, 57, 19, 62, 31, 12, 88, 9, 33, 26, 14, 100, 97, 55, 78, 41, 15, 95, 3, 54, 7, 40, 13, 76, 45, 98]


In [102]:
# Fonction évaluant f en x
# f(Δ) = max(Δ(D, ΠC1), d(Δ, ΠC2))
function f(Δ::AbstractMatrix)::AbstractFloat
    return max(distance(Δ, ΠC1), distance(Δ, ΠC2))
end

function distance(Δ::AbstractMatrix, Π)::AbstractFloat
    return norm(Δ - Π(Δ))
end

function ΠC1(Δ::AbstractMatrix)::AbstractMatrix
    Δ_Sym = (Δ + Δ') / 2
    Δ_Sym = Symmetric(Δ_Sym)
    Σ, P = eigen(Δ_Sym)
    Δ_Sym_Pos = P * Diagonal(max.(0, Σ)) * P'
    return Δ_Sym_Pos
end

function ΠC2(Δ::AbstractMatrix)::AbstractMatrix
    return [(i, j) ∈ Ω ? A[i, j] : Δ[i, j] for i ∈ 1:n, j ∈ 1:n]
end

ΠC2 (generic function with 2 methods)

In [103]:
# Fonction évaluant f en x
# ∂f(D) = ∂d1(D) si (1) ∂d2(D) si (2) 
function ∂f(Δ::AbstractMatrix)::AbstractMatrix
    if distance(Δ, ΠC1) > distance(Δ, ΠC2)
        return ∂d1(Δ)
    else
        return ∂d2(Δ)
    end
end

function ∂d1(Δ::AbstractMatrix)::AbstractMatrix
    return (Δ - ΠC1(Δ)) / norm(Δ - ΠC1(Δ))
end

function ∂d2(Δ::AbstractMatrix)::AbstractMatrix
    return (Δ - ΠC2(Δ)) / norm(Δ - ΠC2(Δ))
end

∂d2 (generic function with 2 methods)

In [104]:
# Algo de sous gradient version notebook
# Choix du pas
pas = 4

# Initialisation
Δ0 = randn(n, n)
Δk = Δ0
Δbest = Δ0
fbest = +Inf
histo = []
itermax = 5000

i = 0
while i < itermax
    i = i + 1
    gk = ∂f(Δk)

    if pas == 1
        Δk -= 1e-2 * gk
    elseif pas == 2
        Δk -= 1 / (100i) * gk
    elseif pas == 3
        Δk -= 1 / (norm(gk, 2) * sqrt(i)) * gk
    elseif pas == 4 #Pas de Poliacov
        Δk -= f(Δk) / norm(gk, 2)^2 * gk
    end

    if f(Δk) < fbest
        fbest = f(Δk)
        Δbest = Δk
    end
    append!(histo, fbest)
end

plot(1:itermax, histo, title = "Convergence curve", label = ["f"], lw = 3, ann = [(55, 80, "Sous-gradient simple")], yaxis = :log)

In [64]:
Δ0 = randn(1000, 1000)
Δ0_Sym = Symmetric(Δ0)
@time eigen(Δ0_Sym);
@time eigen(Δ0);

  0.354700 seconds (14 allocations: 23.248 MiB)
  1.552297 seconds (21 allocations: 31.580 MiB)


In [105]:
function methode_1(Δ0::AbstractVector, itermax::Integer, pas::Integer)
    # Initialisation
    Δk = Δ0
    Δbest = Δ0
    fbest = +Inf
    histo = []
    itermax = 5000

    i = 0
    while i < itermax
        i = i + 1
        gk = ∂f(Δk)

        if pas == 1
            Δk -= 1e-2 * gk
        elseif pas == 2
            Δk -= 1 / (100i) * gk
        elseif pas == 3
            Δk -= 1 / (norm(gk, 2) * sqrt(i)) * gk
        elseif pas == 4 #Pas de Poliacov
            Δk -= f(Δk) / norm(gk, 2)^2 * gk
        end

        if f(Δk) < fbest
            fbest = f(Δk)
            Δbest = Δk
        end
        append!(histo, fbest)
    end

    return histo
end
#plot(1:itermax, methode_1(randn(n, n), itermax, 1), title = "Convergence curve", label = ["f"], lw = 3, ann = [(55, 80, "Sous-gradient simple")], yaxis = :log)

methode_1 (generic function with 2 methods)

In [14]:
println("Erreur relative de symmetrie : $(norm(Δbest - Δbest') / norm(Δbest)) \nEpsilon machine : $(eps(Float64))")

Erreur relative de symmetrie : 7.799103284198431e-17 
Epsilon machine : 2.220446049250313e-16


# Méthodes Alternées

Dans notre cas on optimise sur $$\Delta \in \mathcal{C}=\mathcal{C}_1\bigcap\mathcal{C}_2,$$

Avec : $\mathcal{C}_{1}=\mathcal{S}_{n}^{+}(\mathbb{R})$ et $\mathcal{C}_{2}=\left\{\Delta \in \mathcal{M}_{n}(\mathbb{R}) \text { t.q. } \forall(i, j) \in \Omega, \Delta_{i, j}=A_{i, j}\right\}$.

On optimise donc $$\hspace{5cm} (\mathcal{P})\quad \min_{\Delta \in \mathcal{M}_n(\mathbb{R})} f(\Delta)=\max(d(\Delta,\mathcal{C}_1),d(\Delta,\mathcal{C}_2))$$

Donc soit on rend la matrice plus définis positive avec $\mathcal{C}_1$ ou plus proche de $A$ avec $\mathcal{C}_2$

L'idée des méthode alternées est donc d'optimisé les itérations impaires sur $\mathcal{C}_1$. Et les itérations paiores sur $\mathcal{C}_2$

Algorithme 2: 
- Si itérations impairs $g \in \partial f_1(\Delta)$
- Si itérations pairs $g \in \partial f_2(\Delta)$

Une autre possibilités est Algorithme 3:  Sous gradient projeté (algo 2 + projection sur le $\mathcal{C}_i$ associé)
- Si itérations impairs : $g \in \partial f_1(\Delta)$, puis projection sur $\Pi_{\mathcal{C}_1}$
- Si itérations pairs $g \in \partial f_2(\Delta)$, puis projection sur $\Pi_{\mathcal{C}_2}$

## Algorithme 2

In [15]:
# Algo de sous gradient version notebook
# Choix du pas
pas = 1

# Initialisation
Δ0 = randn(n, n)
Δk = Δ0
Δbest = Δ0
fbest = +Inf
histo = []
itermax = 5000

i = 0
while i < itermax
    i = i + 1
    ## Ajout Algo 2
    # gk = ∂f(Δk)
    if i % 2 == 0
        gk = ∂d1(Δk)
    else
        gk = ∂d2(Δk)
    end
    ## ------------

    if pas == 1
        Δk -= 1e-2 * gk
    elseif pas == 2
        Δk -= 1 / (100i) * gk
    elseif pas == 3
        Δk -= 1 / (norm(gk, 2) * sqrt(i)) * gk
    elseif pas == 4 #Pas de Poliacov
        Δk -= f(Δk) / norm(gk, 2)^2 * gk
    end

    if f(Δk) < fbest
        fbest = f(Δk)
        Δbest = Δk
    end
    append!(histo, fbest)
end

plotly();
iter = 1:itermax;
plot(iter, histo, title = "Convergence curve", label = ["f"], lw = 3, ann = [(55, 80, "Sous-gradient simple")], yaxis = :log)

In [16]:
function methode_2(Δ0, itermax, pas)
    # Initialisation
    Δk = Δ0
    Δbest = Δ0
    fbest = +Inf
    histo = []
    itermax = 5000

    i = 0
    while i < itermax
        i = i + 1
        ## Ajout Algo 2
        # gk = ∂f(Δk)
        if i % 2 == 0
            gk = ∂d1(Δk)
        else
            gk = ∂d2(Δk)
        end
        ## ------------

        if pas == 1
            Δk -= 1e-2 * gk
        elseif pas == 2
            Δk -= 1 / (100i) * gk
        elseif pas == 3
            Δk -= 1 / (norm(gk, 2) * sqrt(i)) * gk
        elseif pas == 4 #Pas de Poliacov
            Δk -= f(Δk) / norm(gk, 2)^2 * gk
        end

        if f(Δk) < fbest
            fbest = f(Δk)
            Δbest = Δk
        end
        append!(histo, fbest)
    end

    return histo
end

methode_2 (generic function with 1 method)

## Algorithme 3

In [17]:
# Algo de sous gradient version notebook
# Choix du pas
pas = 4

# Initialisation
Δ0 = randn(n, n)
Δk = Δ0
Δbest = Δ0
fbest = +Inf
histo = []
itermax = 1000

i = 0
while i < itermax
    i = i + 1
    ## Ajout Algo 2
    # gk = ∂f(Δk)
    if i % 2 == 0
        gk = ∂d1(Δk)
    else
        gk = ∂d2(Δk)
    end
    ## ------------

    if pas == 1
        Δk -= 1e-2 * gk
    elseif pas == 2
        Δk -= 1 / (100i) * gk
    elseif pas == 3
        Δk -= 1 / (norm(gk, 2) * sqrt(i)) * gk
    elseif pas == 4 #Pas de Poliacov
        Δk -= f(Δk) / norm(gk, 2)^2 * gk
    end

    ## Ajout Algo 3
    if i % 2 == 0
        Δk = ΠC1(Δk)
    else
        Δk = ΠC2(Δk)
    end
    ## ------------
    

    if f(Δk) < fbest
        fbest = f(Δk)
        Δbest = Δk
    end
    append!(histo, fbest)
end

plotly();
iter = 1:itermax;
plot(iter, histo, title = "Convergence curve", label = ["f"], lw = 3, ann = [(55, 80, "Sous-gradient simple")], yaxis = :log)

In [18]:
println("Erreur relative de symmetrie : $(norm(Δbest - Δbest') / norm(Δbest)) \nEpsilon machine : $(eps(Float64))")

Erreur relative de symmetrie : 7.72624521682049e-17 
Epsilon machine : 2.220446049250313e-16


In [19]:
function methode_3(Δ0, itermax, pas)
    # Initialisation
    Δk = Δ0
    Δbest = Δ0
    fbest = +Inf
    histo = []
    itermax = 5000

    i = 0
    while i < itermax
        i = i + 1
        ## Ajout Algo 2
        # gk = ∂f(Δk)
        if i % 2 == 0
            gk = ∂d1(Δk)
        else
            gk = ∂d2(Δk)
        end
        ## ------------

        if pas == 1
            Δk -= 1e-2 * gk
        elseif pas == 2
            Δk -= 1 / (100i) * gk
        elseif pas == 3
            Δk -= 1 / (norm(gk, 2) * sqrt(i)) * gk
        elseif pas == 4 #Pas de Poliacov
            Δk -= f(Δk) / norm(gk, 2)^2 * gk
        end

        ## Ajout Algo 3
        if i % 2 == 0
            Δk = ΠC1(Δk)
        else
            Δk = ΠC2(Δk)
        end
        ## ------------

        if f(Δk) < fbest
            fbest = f(Δk)
            Δbest = Δk
        end
        append!(histo, fbest)
    end

    return histo
end

methode_3 (generic function with 1 method)

In [20]:
iter = 1:itermax;
Δ0 = randn(n, n)
pas = 1
histo1 = methode_1(Δ0, itermax, pas)
histo2 = methode_2(Δ0, itermax, pas)
histo3 = methode_3(Δ0, itermax, pas)
plot(title = "Convergence curve")
plot!(1:itermax, [histo1, histo2, histo3], 
    labels = ["methode_1", "methode_2", "methode_3"], 
    lw = 3,
    yaxis = :log)

In [ ]:
iter = 1:itermax;
Δ0 = randn(n, n)
pas = 2
histo1 = methode_1(Δ0, itermax, pas)
histo2 = methode_2(Δ0, itermax, pas)
histo3 = methode_3(Δ0, itermax, pas)
plot(title = "Convergence curve, pas=$(pas)")
plot!(1:itermax, [histo1, histo2, histo3], 
    labels = ["methode_1", "methode_2", "methode_3"], 
    lw = 3,
    yaxis = :log)

LoadError: InterruptException:

In [ ]:
iter = 1:itermax;
Δ0 = randn(n, n)
pas = 3
histo1 = methode_1(Δ0, itermax, pas)
histo2 = methode_2(Δ0, itermax, pas)
histo3 = methode_3(Δ0, itermax, pas)
plot(title = "Convergence curve, pas=$(pas)")
plot!(1:itermax, [histo1, histo2, histo3],
    labels = ["methode_1", "methode_2", "methode_3"],
    lw = 3,
    yaxis = :log)

In [ ]:
iter = 1:itermax;
Δ0 = randn(n, n)
pas = 4
histo1 = methode_1(Δ0, itermax, pas)
histo2 = methode_2(Δ0, itermax, pas)
histo3 = methode_3(Δ0, itermax, pas)
plot(title = "Convergence curve, pas=$(pas)")
plot!(1:itermax, [histo1, histo2, histo3],
    labels = ["methode_1", "methode_2", "methode_3"],
    lw = 3,
    yaxis = :log)

In [ ]:
iter = 1:itermax;
Δ0 = randn(n, n)
pas = 4
histo1 = methode_1(Δ0, itermax, pas)
histo2 = methode_2(Δ0, itermax, pas)
histo3 = methode_3(Δ0, itermax, pas)